In [ ]:
from numpy import array
from keras.preprocessing.text import Tokenizer
from keras.utils import to_categorical
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import LSTM
from keras.layers import Embedding
import pandas as pd


In [ ]:
def generate_seq(model, tokenizer, max_length, seed_text, n_words):
	in_text = seed_text
	# generate a fixed number of words
	for _ in range(n_words):
		# encode the text as integer
		encoded = tokenizer.texts_to_sequences([in_text])[0]
		# pre-pad sequences to a fixed length
		encoded = pad_sequences([encoded], maxlen=max_length, padding='pre')
		# predict probabilities for each word
		yhat = model.predict_classes(encoded, verbose=0)
		# map predicted word index to word
		out_word = ''
		for word, index in tokenizer.word_index.items():
			if index == yhat:
				out_word = word
				break
		# append to input
		in_text += ' ' + out_word
	return in_text

In [ ]:
data = pd.read_csv('/content/spam.csv',encoding='latin-1')
data = data.dropna(how="any", axis=1)
data = data.to_string()
# prepare the tokenizer on the source text
tokenizer = Tokenizer()
tokenizer.fit_on_texts([data])
# determine the vocabulary size
vocab_size = len(tokenizer.word_index) + 1
print('Vocabulary Size: %d' % vocab_size)

Vocabulary Size: 14350


In [ ]:
data

'        v1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              v2\n0      ham                                                                 

In [ ]:
sequences = list()
for line in data.split('\n'):
	encoded = tokenizer.texts_to_sequences([line])[0]
	for i in range(1, len(encoded)):
		sequence = encoded[:i+1]
		sequences.append(sequence)
print('Total Sequences: %d' % len(sequences))

Total Sequences: 93582


In [ ]:
# pad input sequences
max_length = max([len(seq) for seq in sequences])
sequences = pad_sequences(sequences, maxlen=max_length, padding='pre')
print('Max Sequence Length: %d' % max_length)
# split into input and output elements
sequences = array(sequences)
X, y = sequences[:,:-1],sequences[:,-1]
y = to_categorical(y, num_classes=vocab_size)
# define model
model = Sequential()
model.add(Embedding(vocab_size, 10, input_length=max_length-1))
model.add(LSTM(50))
model.add(Dense(vocab_size, activation='softmax'))
print(model.summary())
# compile network
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit network
model.fit(X, y, epochs=500, verbose=1)

2925/2925 [==============================] - 39s 13ms/step - loss: 1.8721 - accuracy: 0.6006
Epoch 286/500
2925/2925 [==============================] - 40s 14ms/step - loss: 1.8581 - accuracy: 0.6044
Epoch 287/500
2925/2925 [==============================] - 40s 14ms/step - loss: 1.8857 - accuracy: 0.5981
Epoch 288/500
2925/2925 [==============================] - 40s 14ms/step - loss: 1.8733 - accuracy: 0.5995
Epoch 289/500
2925/2925 [==============================] - 39s 13ms/step - loss: 1.8762 - accuracy: 0.5982
Epoch 290/500
2925/2925 [==============================] - 39s 13ms/step - loss: 1.8655 - accuracy: 0.6009
Epoch 291/500
2925/2925 [==============================] - 39s 13ms/step - loss: 2.0006 - accuracy: 0.5757
Epoch 292/500
2925/2925 [==============================] - 40s 14ms/step - loss: 1.9077 - accuracy: 0.5931
Epoch 293/500
2925/2925 [==============================] - 40s 14ms/step - loss: 1.8669 - accuracy: 0.6015
Epoch 294/500
2925/2925 [==========================

In [ ]:
# evaluate model
print(generate_seq(model, tokenizer, max_length-1, 'Jack', 4))
print(generate_seq(model, tokenizer, max_length-1, 'Jill', 4))

/usr/local/lib/python3.7/dist-packages/tensorflow/python/keras/engine/sequential.py:450: UserWarning: `model.predict_classes()` is deprecated and will be removed after 2021-01-01. Please use instead:* `np.argmax(model.predict(x), axis=-1)`,   if your model does multi-class classification   (e.g. if it uses a `softmax` last-layer activation).* `(model.predict(x) > 0.5).astype("int32")`,   if your model does binary classification   (e.g. if it uses a `sigmoid` last-layer activation).
  warnings.warn('`model.predict_classes()` is deprecated and '


Jack spam live some new
Jill ham spam hot 25p
